<a href="https://colab.research.google.com/github/Zhairang/CLRS/blob/master/miniChallenge_partII.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from __future__ import print_function
from __future__ import division
# http://pytorch.org/
from os import path
from wheel.pep425tags import get_abbr_impl, get_impl_ver, get_abi_tag
platform = '{}{}-{}'.format(get_abbr_impl(), get_impl_ver(), get_abi_tag())

accelerator = 'cu80' if path.exists('/opt/bin/nvidia-smi') else 'cpu'

!pip install -q http://download.pytorch.org/whl/{accelerator}/torch-0.4.1-{platform}-linux_x86_64.whl torchvision
  
!pip install Pillow==4.1.1
!pip install -U PIL
!pip install -U image

tcmalloc: large alloc 1073750016 bytes == 0x567f4000 @  0x7fbe533d02a4 0x594e17 0x626104 0x51190a 0x4f5277 0x510c78 0x5119bd 0x4f5277 0x4f3338 0x510fb0 0x5119bd 0x4f5277 0x4f3338 0x510fb0 0x5119bd 0x4f5277 0x4f3338 0x510fb0 0x5119bd 0x4f6070 0x510c78 0x5119bd 0x4f5277 0x4f3338 0x510fb0 0x5119bd 0x4f6070 0x4f3338 0x510fb0 0x5119bd 0x4f6070
    100% |████████████████████████████████| 5.7MB 7.2MB/s 
  Found existing installation: Pillow 5.3.0
    Uninstalling Pillow-5.3.0:
      Successfully uninstalled Pillow-5.3.0
  Could not find a version that satisfies the requirement PIL (from versions: )
No matching distribution found for PIL
    100% |████████████████████████████████| 7.3MB 1.0MB/s 


In [2]:
!wget http://6.869.csail.mit.edu/fa18/psets_18/miniplaces2_code.zip miniplaces2_code
!unzip miniplaces2_code

--2018-11-14 00:31:48--  http://6.869.csail.mit.edu/fa18/psets_18/miniplaces2_code.zip
Resolving 6.869.csail.mit.edu (6.869.csail.mit.edu)... 128.30.100.221
Connecting to 6.869.csail.mit.edu (6.869.csail.mit.edu)|128.30.100.221|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 537843272 (513M) [application/zip]
Saving to: ‘miniplaces2_code.zip’

miniplaces2_code.zi 100%[===================>] 512.93M  39.2MB/s    in 14s     

2018-11-14 00:32:02 (37.6 MB/s) - ‘miniplaces2_code.zip’ saved [537843272/537843272]

--2018-11-14 00:32:02--  http://miniplaces2_code/
Resolving miniplaces2_code (miniplaces2_code)... failed: Name or service not known.
wget: unable to resolve host address ‘miniplaces2_code’
FINISHED --2018-11-14 00:32:02--
Total wall clock time: 14s
Downloaded: 1 files, 513M in 14s (37.6 MB/s)
Archive:  miniplaces2_code.zip
   creating: miniplaces_code/
  inflating: miniplaces_code/.DS_Store  
   creating: __MACOSX/
   creating: __MACOSX/miniplaces_code/
  i

In [7]:
ls

__MACOSX/  miniplaces2_code.zip  miniplaces_code/  sample_data/


In [3]:
cd miniplaces_code/


/content/miniplaces_code


0/   15/  21/  28/  34/  40/  47/  53/  6/   66/  72/  79/  85/  91/  98/
1/   16/  22/  29/  35/  41/  48/  54/  60/  67/  73/  8/   86/  92/  99/
10/  17/  23/  3/   36/  42/  49/  55/  61/  68/  74/  80/  87/  93/
11/  18/  24/  30/  37/  43/  5/   56/  62/  69/  75/  81/  88/  94/
12/  19/  25/  31/  38/  44/  50/  57/  63/  7/   76/  82/  89/  95/
13/  2/   26/  32/  39/  45/  51/  58/  64/  70/  77/  83/  9/   96/
14/  20/  27/  33/  4/   46/  52/  59/  65/  71/  78/  84/  90/  97/


In [4]:
ls

data/  dataset.py  models/  train.py


In [0]:
import torch
import torchvision.transforms as transforms

from scipy.misc import imread, imresize

# part II  

In [0]:



import gc
import sys
from torch.autograd import Variable
import torch
import torch.nn as nn
import torch.optim as optim
import torch.optim.lr_scheduler
torch.backends.cudnn.benchmark=True
import numpy as np 

import dataset
from models.AlexNet import *
from models.ResNet import *

def run():
    # Parameters
    num_epochs = 150   #-------------------- made change
    output_period = 100
    batch_size = 100

    # setup the device for running
    device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
    model = resnet_18()
    model = model.to(device)

    train_loader, val_loader = dataset.get_data_loaders(batch_size)
    num_train_batches = len(train_loader)
    num_val_batches = len(val_loader)   #-------------------- made change

    criterion = nn.CrossEntropyLoss().to(device)
    # TODO: optimizer is currently unoptimized
    # there's a lot of room for improvement/different optimizers
    optimizer = optim.SGD(model.parameters(), lr=1e-1 ) #1e-4   #-------------- made change
    
    
    epoch = 1
    
    
    #-------------- made change    
    storetrain_loss= np.zeros(150*10)
    storetrain_acc= np.zeros(150*10)
    storeval_loss= np.zeros(150*10)
    storeval_acc= np.zeros(150*10) 

    
    
    while epoch <= num_epochs:
        running_loss = 0.0
        for param_group in optimizer.param_groups:
            print('Current learning rate: ' + str(param_group['lr']))
        model.train()

        #-------------------
        running_acc=0 
        for batch_num, (inputs, labels) in enumerate(train_loader, 1):
            inputs = inputs.to(device)
            labels = labels.to(device)

            optimizer.zero_grad()
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()
            running_loss += loss.item()

            
            #------------------
            acc = accuracy(outputs,labels)[0]
            running_acc = running_acc + acc.cpu().numpy()[0] 
            #print("accuracy", acc.cpu().numpy()[0])

            if batch_num % output_period == 0:
                print('[%d:%.2f] loss: %.3f ,acc:%.3f' % (
                    epoch, batch_num*1.0/num_train_batches,
                    running_loss/output_period,
                    running_acc /output_period                    
                    
                    ))
                
                #print((epoch-1)*10+batch_num*1.0/num_train_batches*10)
                storetrain_loss[int((epoch-1)*10+batch_num*1.0/num_train_batches*10)]= running_loss/output_period
                storetrain_acc[int((epoch-1)*10+batch_num*1.0/num_train_batches*10)]= running_acc /output_period    
      
                
                
                
                running_loss = 0.0
                running_acc  = 0.0
                           
                gc.collect()
               

        gc.collect()
        # save after every epoch
        torch.save(model.state_dict(), "models/model.%d" % epoch)

        # TODO: Calculate classification error and Top-5 Error -----------------------------
        # on training and validation datasets here
        
        
        #valditation : 
        #-------------------
        running_acc=0 
        for batch_num, (inputs, labels) in enumerate(val_loader, 1):
            inputs = inputs.to(device)
            labels = labels.to(device)

            optimizer.zero_grad()
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            #  loss.backward()
            optimizer.step()
            running_loss += loss.item()

            
            #------------------
            acc = accuracy(outputs,labels)[0]
            running_acc = running_acc + acc.cpu().numpy()[0] 
            #print("accuracy", acc.cpu().numpy()[0])

            if batch_num % output_period == 0:
                print("validation:")
                print('[%d:%.2f] loss: %.3f ,acc:%.3f' % (
                    epoch, batch_num*1.0/num_val_batches,
                    running_loss/output_period,
                    running_acc /output_period                    
                    
                    ))
                
                storeval_loss[int((epoch-1)*10+batch_num*1.0/num_val_batches*10)]= running_loss/output_period
                storeval_acc[int((epoch-1)*10+batch_num*1.0/num_val_batches*10)]= running_acc /output_period                  
                
                
                running_loss = 0.0
                running_acc  = 0.0
                           
                gc.collect()           
         
        
        
        
        
        
        gc.collect()
        epoch += 1


    print('final results:')
    

#--------------------------------------------------------- made change
# ''''''''''''''  calculate accuracy  '''''''''''''''''''''''''''''''''''''''''''''''''''''''''''''  code from https://github.com/pytorch/examples/blob/master/imagenet/main.py

def accuracy(output, target, topk=(5,)):
    """Computes the accuracy over the k top predictions for the specified values of k"""
    with torch.no_grad():
        maxk = max(topk)
        batch_size = target.size(0)
        
        _, pred = output.topk(maxk, 1, True, True)
        pred = pred.t()
        correct = pred.eq(target.view(1, -1).expand_as(pred))
        
        res = []
        for k in topk:
            correct_k = correct[:k].view(-1).float().sum(0, keepdim=True)
            res.append(correct_k.mul_(100.0 / batch_size))
        return res
      
      
      

print('Starting training')
run()
print('Training terminated')



Starting training
Current learning rate: 0.001
[1:0.10] loss: 4.684
[1:0.20] loss: 4.633
[1:0.30] loss: 4.607
[1:0.40] loss: 4.592
[1:0.50] loss: 4.576
[1:0.60] loss: 4.569
[1:0.70] loss: 4.557
[1:0.80] loss: 4.544
[1:0.90] loss: 4.535
[1:1.00] loss: 4.521
Current learning rate: 0.001
[2:0.10] loss: 4.511
[2:0.20] loss: 4.495
[2:0.30] loss: 4.493
[2:0.40] loss: 4.476
[2:0.50] loss: 4.464
[2:0.60] loss: 4.451
[2:0.70] loss: 4.434
[2:0.80] loss: 4.427
[2:0.90] loss: 4.414
[2:1.00] loss: 4.394
Current learning rate: 0.001
[3:0.10] loss: 4.369
[3:0.20] loss: 4.356
[3:0.30] loss: 4.345
[3:0.40] loss: 4.330
[3:0.50] loss: 4.315
[3:0.60] loss: 4.299
[3:0.70] loss: 4.276
[3:0.80] loss: 4.259
[3:0.90] loss: 4.239
[3:1.00] loss: 4.235
Current learning rate: 0.001
[4:0.10] loss: 4.217
[4:0.20] loss: 4.209
[4:0.30] loss: 4.188
[4:0.40] loss: 4.189
[4:0.50] loss: 4.165
[4:0.60] loss: 4.165
[4:0.70] loss: 4.156
[4:0.80] loss: 4.137
[4:0.90] loss: 4.119
[4:1.00] loss: 4.110
Current learning rate: 0.0

In [38]:
ls

0/   15/  21/  28/  34/  40/  47/  53/  6/   66/  72/  79/  85/  91/  98/
1/   16/  22/  29/  35/  41/  48/  54/  60/  67/  73/  8/   86/  92/  99/
10/  17/  23/  3/   36/  42/  49/  55/  61/  68/  74/  80/  87/  93/
11/  18/  24/  30/  37/  43/  5/   56/  62/  69/  75/  81/  88/  94/
12/  19/  25/  31/  38/  44/  50/  57/  63/  7/   76/  82/  89/  95/
13/  2/   26/  32/  39/  45/  51/  58/  64/  70/  77/  83/  9/   96/
14/  20/  27/  33/  4/   46/  52/  59/  65/  71/  78/  84/  90/  97/


In [0]:

# Add Weight Decay and Change Learning Rate
# Change Optimizers/Add Schedulers



import gc
import sys
from torch.autograd import Variable
import torch
import torch.nn as nn
import torch.optim as optim
import torch.optim.lr_scheduler
torch.backends.cudnn.benchmark=True
import numpy as np 

import dataset
from models.AlexNet import *
from models.ResNet import *

def run():
    # Parameters
    num_epochs = 150   #-------------------- made change
    output_period = 100
    batch_size = 100

    # setup the device for running
    device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
    model = resnet_18()
    model = model.to(device)

    train_loader, val_loader = dataset.get_data_loaders(batch_size)
    num_train_batches = len(train_loader)
    num_val_batches = len(val_loader)   #-------------------- made change

    criterion = nn.CrossEntropyLoss().to(device)
    # TODO: optimizer is currently unoptimized
    # there's a lot of room for improvement/different optimizers
    optimizer = optim.SGD(model.parameters(), lr=1e-1,weight_decay=5e-4 ) #1e-4   #-------------- made change
    
    #scheduler ``````   #-------------- made change
    scheduler = torch.optim.lr_scheduler.MultiStepLR(optimizer, milestones=[50,100], gamma=0.1)
    
    epoch = 1
    
    
    #-------------- made change    
    storetrain_loss= np.zeros(150*10)
    storetrain_acc= np.zeros(150*10)
    storeval_loss= np.zeros(150*10)
    storeval_acc= np.zeros(150*10) 

    
    
    while epoch <= num_epochs:
        scheduler.step()   #--------------------------------------------------------- made change
        running_loss = 0.0
        for param_group in optimizer.param_groups:
            print('Current learning rate: ' + str(param_group['lr']))
        model.train()

        #-------------------
        running_acc=0 
        for batch_num, (inputs, labels) in enumerate(train_loader, 1):
            inputs = inputs.to(device)
            labels = labels.to(device)

            optimizer.zero_grad()
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()
            running_loss += loss.item()

            
            #------------------
            acc = accuracy(outputs,labels)[0]
            running_acc = running_acc + acc.cpu().numpy()[0] 
            #print("accuracy", acc.cpu().numpy()[0])

            if batch_num % output_period == 0:
                print('[%d:%.2f] loss: %.3f ,acc:%.3f' % (
                    epoch, batch_num*1.0/num_train_batches,
                    running_loss/output_period,
                    running_acc /output_period                    
                    
                    ))
                
                #print((epoch-1)*10+batch_num*1.0/num_train_batches*10)
                storetrain_loss[int((epoch-1)*10+batch_num*1.0/num_train_batches*10)]= running_loss/output_period
                storetrain_acc[int((epoch-1)*10+batch_num*1.0/num_train_batches*10)]= running_acc /output_period    
      
                
                
                
                running_loss = 0.0
                running_acc  = 0.0
                           
                gc.collect()
               

        gc.collect()
        # save after every epoch
        torch.save(model.state_dict(), "models/model.%d" % epoch)

        # TODO: Calculate classification error and Top-5 Error -----------------------------
        # on training and validation datasets here
        
        
        #valditation : 
        #-------------------
        running_acc=0 
        for batch_num, (inputs, labels) in enumerate(val_loader, 1):
            inputs = inputs.to(device)
            labels = labels.to(device)

            optimizer.zero_grad()
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            #  loss.backward()
            optimizer.step()
            running_loss += loss.item()

            
            #------------------
            acc = accuracy(outputs,labels)[0]
            running_acc = running_acc + acc.cpu().numpy()[0] 
            #print("accuracy", acc.cpu().numpy()[0])

            if batch_num % output_period == 0:
                print("validation:")
                print('[%d:%.2f] loss: %.3f ,acc:%.3f' % (
                    epoch, batch_num*1.0/num_val_batches,
                    running_loss/output_period,
                    running_acc /output_period                    
                    
                    ))
                
                storeval_loss[int((epoch-1)*10+batch_num*1.0/num_val_batches*10)]= running_loss/output_period
                storeval_acc[int((epoch-1)*10+batch_num*1.0/num_val_batches*10)]= running_acc /output_period                  
                
                
                running_loss = 0.0
                running_acc  = 0.0
                           
                gc.collect()           
         
        
        
        
        
        
        gc.collect()
        epoch += 1




#--------------------------------------------------------- made change
# ''''''''''''''  calculate accuracy  '''''''''''''''''''''''''''''''''''''''''''''''''''''''''''''  code from https://github.com/pytorch/examples/blob/master/imagenet/main.py

def accuracy(output, target, topk=(5,)):
    """Computes the accuracy over the k top predictions for the specified values of k"""
    with torch.no_grad():
        maxk = max(topk)
        batch_size = target.size(0)
        
        _, pred = output.topk(maxk, 1, True, True)
        pred = pred.t()
        correct = pred.eq(target.view(1, -1).expand_as(pred))
        
        res = []
        for k in topk:
            correct_k = correct[:k].view(-1).float().sum(0, keepdim=True)
            res.append(correct_k.mul_(100.0 / batch_size))
        return res
      
      
      

print('Starting training')
run()
print('Training terminated')

